# Classification des Micro-régions de Corse par K-NN

Ce notebook implémente un système de classification des micro-régions corses basé sur l'algorithme des k plus proches voisins (k-NN). Cliquez sur la carte pour identifier la micro-région correspondante.

**Fichiers nécessaires :**
- `communes-de-corse-en-corse-et-francais.csv` : Liste des communes avec coordonnées GPS
- `communes-par-territoire-de-projet-de-la-collectivite-territoriale-de-corse0.csv` : Territoires de projet par commune

In [ ]:
# Installation des bibliothèques nécessaires
!pip install folium pandas numpy scikit-learn --quiet

In [ ]:
import pandas as pd
import numpy as np
import folium
from sklearn.neighbors import KNeighborsClassifier
from IPython.display import display, HTML
import json
import re

## 1. Chargement et préparation des données

In [ ]:
# Chargement du fichier avec les coordonnées GPS
df_coords = pd.read_csv('communes-de-corse-en-corse-et-francais.csv', 
                        sep=';', encoding='utf-8')

print(f"Fichier coordonnées: {len(df_coords)} communes")
print("\nPremières lignes:")
display(df_coords.head())
print("\nColonnes disponibles:")
print(df_coords.columns.tolist())

In [ ]:
# Chargement du fichier avec les territoires de projet
df_territoires = pd.read_csv('communes-par-territoire-de-projet-de-la-collectivite-territoriale-de-corse0.csv',
                             sep=';', encoding='utf-8')

print(f"Fichier territoires: {len(df_territoires)} communes")
print("\nPremières lignes:")
display(df_territoires.head())
print("\nTerritoires de projet (micro-régions):")
print(sorted(df_territoires['Territoire de projet'].unique()))

## 2. Extraction des coordonnées GPS

In [ ]:
def extract_coordinates(point_geo_str):
    """
    Extrait latitude et longitude de la colonne Point_Geo
    Format attendu: "41.984099158, 8.798384636"
    """
    if pd.isna(point_geo_str):
        return None, None
    
    try:
        # Supprimer les espaces et split par virgule
        coords = str(point_geo_str).strip().split(',')
        if len(coords) == 2:
            lat = float(coords[0].strip())
            lon = float(coords[1].strip())
            return lat, lon
    except:
        pass
    
    return None, None

# Extraction des coordonnées
df_coords[['Latitude', 'Longitude']] = df_coords['Point_Geo'].apply(
    lambda x: pd.Series(extract_coordinates(x))
)

# Vérification
print("Extraction des coordonnées:")
print(f"Communes avec coordonnées: {df_coords['Latitude'].notna().sum()}/{len(df_coords)}")
print("\nExemple:")
display(df_coords[['Nom français', 'Latitude', 'Longitude']].head())

## 3. Fusion des deux fichiers

In [ ]:
# Normalisation des noms de communes pour la jointure
def normalize_commune_name(name):
    """
    Normalise le nom d'une commune pour faciliter la jointure
    """
    if pd.isna(name):
        return ''
    # Convertir en majuscules et supprimer les espaces multiples
    return str(name).upper().strip()

df_coords['Commune_norm'] = df_coords['Nom français'].apply(normalize_commune_name)
df_territoires['Commune_norm'] = df_territoires['Commune'].apply(normalize_commune_name)

# Fusion des deux dataframes
df = pd.merge(
    df_coords,
    df_territoires[['Commune_norm', 'Territoire de projet']],
    on='Commune_norm',
    how='inner'
)

# Renommer pour cohérence
df['Commune'] = df['Nom français']

print(f"Fusion réussie: {len(df)} communes avec coordonnées ET territoire de projet")
print("\nAperçu des données fusionnées:")
display(df[['Commune', 'Latitude', 'Longitude', 'Territoire de projet']].head(10))

In [ ]:
# Nettoyage: supprimer les lignes sans coordonnées
df_clean = df.dropna(subset=['Latitude', 'Longitude', 'Territoire de projet']).copy()

print(f"\n✅ Données finales: {len(df_clean)} communes prêtes pour la classification")
print(f"\nRépartition par micro-région:")
print(df_clean['Territoire de projet'].value_counts().sort_index())

## 4. Entraînement du modèle k-NN

In [ ]:
# Préparation des données pour k-NN
X = df_clean[['Latitude', 'Longitude']].values
y = df_clean['Territoire de projet'].values

# Création du modèle k-NN avec k=5 (ajustable)
k = 5
knn = KNeighborsClassifier(n_neighbors=k, weights='distance', metric='haversine')

# Conversion des coordonnées en radians pour la distance haversine
X_rad = np.radians(X)

# Entraînement du modèle
knn.fit(X_rad, y)

print(f"✅ Modèle k-NN entraîné avec k={k} voisins")
print(f"📊 Nombre de micro-régions: {len(np.unique(y))}")
print(f"\n🗺️ Micro-régions identifiées:")
for i, region in enumerate(sorted(np.unique(y)), 1):
    count = (y == region).sum()
    print(f"  {i:2d}. {region} ({count} communes)")

## 5. Création de la carte interactive avec Folium

In [ ]:
# Couleurs pour chaque micro-région
microregions = sorted(df_clean['Territoire de projet'].unique())
colors = ['red', 'blue', 'green', 'purple', 'orange', 'darkred', 
          'lightred', 'beige', 'darkblue', 'darkgreen', 'cadetblue', 
          'darkpurple', 'pink', 'lightblue', 'lightgreen', 'gray', 'black', 'lightgray']

color_map = {region: colors[i % len(colors)] for i, region in enumerate(microregions)}

print("🎨 Carte des couleurs par micro-région:")
for region, color in sorted(color_map.items()):
    print(f"  • {region}: {color}")

In [ ]:
# Coordonnées du centre de la Corse
center_lat = df_clean['Latitude'].mean()
center_lon = df_clean['Longitude'].mean()

print(f"Centre de la carte: {center_lat:.4f}°N, {center_lon:.4f}°E")

## 6. Carte interactive avec prédiction au clic

In [ ]:
# Création de la carte interactive
m_interactive = folium.Map(
    location=[center_lat, center_lon],
    zoom_start=9,
    tiles='OpenStreetMap'
)

# Ajout des marqueurs pour chaque commune
for idx, row in df_clean.iterrows():
    folium.CircleMarker(
        location=[row['Latitude'], row['Longitude']],
        radius=3,
        popup=f"<b>{row['Commune']}</b><br>{row['Territoire de projet']}<br><small>({row['Latitude']:.4f}, {row['Longitude']:.4f})</small>",
        tooltip=row['Commune'],
        color=color_map[row['Territoire de projet']],
        fill=True,
        fillColor=color_map[row['Territoire de projet']],
        fillOpacity=0.7
    ).add_to(m_interactive)

# Préparer les données des communes pour JavaScript
communes_data = df_clean[['Latitude', 'Longitude', 'Commune', 'Territoire de projet']].to_dict('records')

# JavaScript pour la prédiction k-NN au clic
click_js = f"""
<script>
// Données des communes
var communesData = {json.dumps(communes_data)};

// Carte des couleurs
var colorMap = {json.dumps(color_map)};

// Fonction pour calculer la distance haversine
function haversineDistance(lat1, lon1, lat2, lon2) {{
    const R = 6371; // Rayon de la Terre en km
    const dLat = (lat2 - lat1) * Math.PI / 180;
    const dLon = (lon2 - lon1) * Math.PI / 180;
    const a = Math.sin(dLat/2) * Math.sin(dLat/2) +
              Math.cos(lat1 * Math.PI / 180) * Math.cos(lat2 * Math.PI / 180) *
              Math.sin(dLon/2) * Math.sin(dLon/2);
    const c = 2 * Math.atan2(Math.sqrt(a), Math.sqrt(1-a));
    return R * c;
}}

// Fonction k-NN
function predictRegion(lat, lon, k) {{
    // Calculer les distances
    var distances = communesData.map(function(commune) {{
        return {{
            distance: haversineDistance(lat, lon, commune.Latitude, commune.Longitude),
            region: commune['Territoire de projet'],
            commune: commune.Commune
        }};
    }});
    
    // Trier par distance
    distances.sort((a, b) => a.distance - b.distance);
    
    // Prendre les k plus proches
    var kNearest = distances.slice(0, k);
    
    // Vote pondéré par l'inverse de la distance
    var votes = {{}};
    kNearest.forEach(function(neighbor) {{
        var weight = 1 / (neighbor.distance + 0.001); // +0.001 pour éviter division par 0
        if (votes[neighbor.region]) {{
            votes[neighbor.region] += weight;
        }} else {{
            votes[neighbor.region] = weight;
        }}
    }});
    
    // Trouver la région gagnante
    var maxVote = 0;
    var predictedRegion = '';
    for (var region in votes) {{
        if (votes[region] > maxVote) {{
            maxVote = votes[region];
            predictedRegion = region;
        }}
    }}
    
    return {{
        region: predictedRegion,
        neighbors: kNearest
    }};
}}

// Variable pour stocker le marqueur de prédiction
var predictionMarker = null;
var neighborLines = [];

// Attendre que la carte soit chargée
setTimeout(function() {{
    var maps = document.querySelectorAll('.folium-map');
    if (maps.length > 0) {{
        var mapElement = maps[maps.length - 1];
        var leafletMap = mapElement._leaflet_map;
        
        if (leafletMap) {{
            leafletMap.on('click', function(e) {{
                var lat = e.latlng.lat;
                var lon = e.latlng.lng;
                
                // Prédiction avec k={k}
                var result = predictRegion(lat, lon, {k});
                
                // Supprimer l'ancien marqueur et lignes
                if (predictionMarker) {{
                    leafletMap.removeLayer(predictionMarker);
                }}
                neighborLines.forEach(function(line) {{
                    leafletMap.removeLayer(line);
                }});
                neighborLines = [];
                
                // Créer le popup avec informations détaillées
                var popupContent = '<div style="min-width: 200px;">' +
                    '<h4 style="margin: 5px 0; color: ' + colorMap[result.region] + ';">🎯 ' + result.region + '</h4>' +
                    '<p style="margin: 5px 0; font-size: 11px;"><b>Coordonnées cliquées:</b><br>' + 
                    'Lat: ' + lat.toFixed(5) + '°<br>Lon: ' + lon.toFixed(5) + '°</p>' +
                    '<hr style="margin: 5px 0;">' +
                    '<p style="margin: 5px 0; font-size: 11px;"><b>{k} plus proches communes:</b></p>' +
                    '<ul style="margin: 5px 0; padding-left: 20px; font-size: 10px;">';
                
                result.neighbors.forEach(function(neighbor, i) {{
                    popupContent += '<li><b>' + neighbor.commune + '</b> (' + neighbor.distance.toFixed(2) + ' km)</li>';
                }});
                
                popupContent += '</ul></div>';
                
                // Ajouter le nouveau marqueur
                predictionMarker = L.marker([lat, lon], {{
                    icon: L.divIcon({{
                        className: 'prediction-marker',
                        html: '<div style="background-color: ' + colorMap[result.region] + 
                              '; width: 20px; height: 20px; border-radius: 50%; ' +
                              'border: 3px solid white; box-shadow: 0 0 10px rgba(0,0,0,0.5);"></div>',
                        iconSize: [20, 20]
                    }})
                }}).addTo(leafletMap);
                
                predictionMarker.bindPopup(popupContent, {{maxWidth: 300}}).openPopup();
                
                // Ajouter des lignes vers les k plus proches voisins
                result.neighbors.forEach(function(neighbor) {{
                    var commune = communesData.find(c => c.Commune === neighbor.commune);
                    if (commune) {{
                        var line = L.polyline(
                            [[lat, lon], [commune.Latitude, commune.Longitude]],
                            {{
                                color: 'gray',
                                weight: 1,
                                opacity: 0.5,
                                dashArray: '5, 5'
                            }}
                        ).addTo(leafletMap);
                        neighborLines.push(line);
                    }}
                }});
            }});
            
            console.log('✅ Gestionnaire de clic k-NN activé');
            console.log('📊 ' + communesData.length + ' communes chargées');
        }}
    }}
}}, 1000);
</script>
"""

m_interactive.get_root().html.add_child(folium.Element(click_js))

# Ajout de la légende
legend_html = '''
<div style="position: fixed; 
            top: 10px; right: 10px; width: 250px; max-height: 85vh; overflow-y: auto;
            background-color: white; border:2px solid grey; z-index:9999; border-radius: 5px;
            font-size:12px; padding: 10px; box-shadow: 0 0 15px rgba(0,0,0,0.2);">
<p style="margin-bottom: 8px; font-weight: bold; font-size: 14px;">🗺️ Micro-régions de Corse</p>
'''

for region, color in sorted(color_map.items()):
    legend_html += f'<p style="margin: 3px 0;"><i class="fa fa-circle" style="color:{color}"></i> {region}</p>'

legend_html += f'<hr style="margin: 8px 0;"><p style="margin: 3px 0; font-size: 11px; color: #666;">k = {k} voisins<br>Distance: Haversine</p></div>'

m_interactive.get_root().html.add_child(folium.Element(legend_html))

# Ajout d'instructions
instructions_html = '''
<div style="position: fixed; 
            bottom: 10px; left: 10px; width: 320px; 
            background-color: white; border:2px solid grey; z-index:9999; border-radius: 5px;
            font-size:13px; padding: 12px; box-shadow: 0 0 15px rgba(0,0,0,0.2);">
<p style="margin: 0 0 8px 0; font-weight: bold;">🖱️ Mode d'emploi</p>
<p style="margin: 5px 0; line-height: 1.4;"><b>Cliquez</b> n'importe où sur la carte pour prédire la micro-région.</p>
<p style="margin: 5px 0; line-height: 1.4; font-size: 11px;">• Un marqueur coloré apparaît au point cliqué<br>
• Les lignes pointillées montrent les k communes les plus proches<br>
• Le popup affiche la prédiction détaillée</p>
</div>
'''

m_interactive.get_root().html.add_child(folium.Element(instructions_html))

print("\n✅ Carte interactive créée avec succès!")
print(f"\n🖱️ Cliquez sur n'importe quel point de la carte pour prédire sa micro-région avec k={k} voisins.")

In [ ]:
# Affichage de la carte interactive
m_interactive

## 7. Sauvegarde de la carte

In [ ]:
# Sauvegarder la carte interactive
m_interactive.save('carte_corse_knn_interactive.html')
print("✅ Carte sauvegardée dans 'carte_corse_knn_interactive.html'")
print("📁 Vous pouvez ouvrir ce fichier dans un navigateur pour une utilisation autonome.")

## 8. Test de la prédiction (optionnel)

In [ ]:
# Fonction pour tester la prédiction sur des coordonnées spécifiques
def predict_region(lat, lon, k_value=5):
    """
    Prédit la micro-région pour des coordonnées données
    """
    # Conversion en radians
    coords_rad = np.radians([[lat, lon]])
    
    # Prédiction
    prediction = knn.predict(coords_rad)[0]
    
    # Trouver les k plus proches voisins
    distances, indices = knn.kneighbors(coords_rad)
    
    # Convertir les distances de radians en km
    distances_km = distances[0] * 6371  # Rayon de la Terre en km
    
    print(f"\n📍 Coordonnées: {lat:.5f}°N, {lon:.5f}°E")
    print(f"🎯 Micro-région prédite: {prediction}")
    print(f"\n{k_value} plus proches communes:")
    
    for i, idx in enumerate(indices[0]):
        commune_info = df_clean.iloc[idx]
        print(f"  {i+1}. {commune_info['Commune']:30s} ({commune_info['Territoire de projet']:30s}) - {distances_km[i]:6.2f} km")
    
    return prediction

# Exemples de test
print("=" * 100)
print("TESTS DE PRÉDICTION k-NN")
print("=" * 100)

# Test 1: Centre approximatif de la Corse (vers Corte)
print("\n🔍 Test 1: Centre de la Corse")
predict_region(42.15, 9.15, k)

# Test 2: Nord de la Corse (Balagne/Bastia)
print("\n🔍 Test 2: Nord de la Corse")
predict_region(42.55, 8.85, k)

# Test 3: Sud de la Corse (vers Porto-Vecchio)
print("\n🔍 Test 3: Sud de la Corse")
predict_region(41.65, 9.15, k)

# Test 4: Ouest (vers Ajaccio)
print("\n🔍 Test 4: Ouest de la Corse (Ajaccio)")
predict_region(41.93, 8.74, k)

## 9. Analyse de performance (optionnel)

In [ ]:
# Évaluation de la cohérence du modèle (cross-validation)
from sklearn.model_selection import cross_val_score

# Test avec différentes valeurs de k
k_values = [3, 5, 7, 9, 11, 15]
scores = []

print("📊 Évaluation de la précision pour différentes valeurs de k:\n")
print(f"{'k':<5} {'Précision moyenne':<20} {'Écart-type':<15}")
print("-" * 50)

for k_val in k_values:
    knn_temp = KNeighborsClassifier(n_neighbors=k_val, weights='distance', metric='haversine')
    cv_scores = cross_val_score(knn_temp, X_rad, y, cv=5)
    mean_score = cv_scores.mean()
    std_score = cv_scores.std()
    scores.append(mean_score)
    print(f"{k_val:<5} {mean_score:.4f} ({mean_score*100:5.2f}%)     ± {std_score:.4f}")

best_k = k_values[scores.index(max(scores))]
best_score = max(scores)
print("\n" + "=" * 50)
print(f"✨ Meilleure valeur de k: {best_k} (précision: {best_score:.4f} / {best_score*100:.2f}%)")
print("=" * 50)

## 10. Statistiques par micro-région

In [ ]:
# Statistiques descriptives par micro-région
print("📈 STATISTIQUES PAR MICRO-RÉGION\n")
print(f"{'Micro-région':<35} {'Nb communes':<15} {'% du total'}")
print("=" * 65)

total_communes = len(df_clean)
stats = df_clean['Territoire de projet'].value_counts().sort_index()

for region, count in stats.items():
    pct = (count / total_communes) * 100
    print(f"{region:<35} {count:<15} {pct:>5.1f}%")

print("=" * 65)
print(f"{'TOTAL':<35} {total_communes:<15} 100.0%")

## Conclusion

✅ **Notebook k-NN Corse - Résumé**

Ce notebook implémente un classificateur k-NN pour les micro-régions de Corse avec:
1. ✅ Chargement des données depuis 2 fichiers CSV (coordonnées + territoires)
2. ✅ Extraction automatique des coordonnées GPS depuis la colonne Point_Geo
3. ✅ Fusion intelligente des deux sources de données
4. ✅ Entraînement d'un modèle k-NN avec distance haversine
5. ✅ Carte interactive Folium avec prédiction au clic
6. ✅ Visualisation des k plus proches voisins
7. ✅ Tests de performance et validation
8. ✅ Export HTML pour utilisation autonome

**🖱️ Utilisation:**
- Cliquez n'importe où sur la carte
- Un marqueur coloré apparaît avec la micro-région prédite
- Des lignes pointillées montrent les k communes les plus proches
- Un popup détaille la prédiction et les voisins

**📁 Fichier exporté:** `carte_corse_knn_interactive.html`

La carte HTML peut être ouverte dans n'importe quel navigateur pour une utilisation autonome!